# Safe Synthetics Hyperparameter Optimization with Weights & Biases

This notebook demonstrates how to optimize Safe Synthetics model parameters using Weights & Biases (W&B) sweeps for automated hyperparameter tuning.

## What this notebook does:

**🎯 Automated Parameter Optimization**: Uses Bayesian optimization to find the best Safe Synthetics parameters for your dataset

**📊 Built-in Evaluation**: Leverages Safe Synthetics' automatic data quality evaluation and reporting

**🔍 Tracking**: Logs all experiments, parameters, and quality scores to W&B for easy comparison and analysis

## How it works:
1. **Configure** your dataset and optimization parameters
2. **Launch** multiple Safe Synthetics training jobs with different parameter combinations  
3. **Evaluate** synthetic data quality automatically using built-in metrics
4. **Optimize** parameters based on quality scores using Bayesian optimization
5. **Analyze** results through W&B's visualization dashboard


## 1) Install Dependencies

Install the required Python packages for Safe Synthetics and Weights & Biases integration.


In [1]:
%%capture
%pip install -U gretel-client wandb

## 2) Configure Gretel & Weights & Biases

Set up authentication and project configuration for both Gretel and W&B services. The notebook will prompt for API keys if not already configured in your environment.

**Configuration Options**:
- `MAX_TRIALS`: Number of different parameter combinations to test (default: 2)  


In [2]:
import os, json, pathlib, uuid, time
from typing import Any, Dict, Optional
import pandas as pd
import concurrent.futures
import threading
from queue import Queue

# Gretel Navigator client
from gretel_client.navigator_client import Gretel

# --- Gretel config ---
DEFAULT_PROJECT_ID = os.getenv("GRETEL_PROJECT", "safe-syn-sweeps")
gretel = Gretel(api_key="prompt", default_project_id=DEFAULT_PROJECT_ID)

# --- W&B config login ---
import wandb
from getpass import getpass

WANDB_PROJECT = os.getenv("WANDB_PROJECT", "safe-syn-sweeps")
WANDB_ENTITY  = os.getenv("WANDB_ENTITY", None)  # optional
RUN_PREFIX    = os.getenv("RUN_PREFIX", "safe-syn")
MAX_TRIALS    = int(os.getenv("MAX_TRIALS", "2"))  # Number of parameter combinations to test

# Prompt for W&B API key if not already set
wandb_api_key = os.getenv("WANDB_API_KEY")
if not wandb_api_key:
    try:
        wandb_api_key = getpass("Enter your Weights & Biases API key: ")
    except Exception:
        wandb_api_key = input("Enter your Weights & Biases API key: ")
wandb.login(key=wandb_api_key)

# Resolve default entity if none provided
api = wandb.Api()
if WANDB_ENTITY is None:
    try:
        WANDB_ENTITY = api.default_entity
    except Exception:
        WANDB_ENTITY = None

print(f"✅ Configured Gretel project: {DEFAULT_PROJECT_ID}")
print(f"✅ Configured W&B project: {WANDB_PROJECT}")
print(f"✅ Entity: {WANDB_ENTITY}")


Logged in as yamini@gretel.ai ✅
Using project: safe-syn-sweeps-ff62124b804335a
Project link: https://console.gretel.ai/proj_31FkDXkE3FFoXai92RsAAeoLW5l


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /Users/ykagal/.netrc
wandb: Currently logged in as: yamini_gretel to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


✅ Configured Gretel project: safe-syn-sweeps
✅ Configured W&B project: safe-syn-sweeps
✅ Entity: yamini_gretel


## 3) Load Your Dataset

Specify your training dataset for Safe Synthetics optimization. You can use the default public dataset or point to your own CSV/Parquet file by setting the `TRAINING_DATA_SOURCE` environment variable.


In [3]:
# Use the same public dataset or point to your own CSV/Parquet file
TRAINING_DATA_SOURCE = os.getenv(
    "TRAINING_DATA_SOURCE",
    "https://gretel-datasets.s3.us-west-2.amazonaws.com/ecommerce_customers.csv",
)

df = pd.read_csv(TRAINING_DATA_SOURCE)
print(f"Loaded training data with {len(df):,} rows and {len(df.columns)} columns")
print(f"Columns: {list(df.columns)}")
df.head()


Loaded training data with 500 rows and 8 columns
Columns: ['Email', 'Address', 'Avatar', 'Avg. Session Length', 'Time on App', 'Time on Website', 'Length of Membership', 'Yearly Amount Spent']


Email  \
0      mstephenson@fernandez.com   
1              hduke@hotmail.com   
2               pallen@yahoo.com   
3        riverarebecca@gmail.com   
4  mstephens@davidson-herman.com   

                                             Address            Avatar  \
0       835 Frank Tunnel\nWrightmouth, MI 82180-9605            Violet   
1     4547 Archer Common\nDiazchester, CA 06566-8576         DarkGreen   
2  24645 Valerie Unions Suite 582\nCobbborough, D...            Bisque   
3   1414 David Throughway\nPort Jason, OH 22070-1220       SaddleBrown   
4  14023 Rodriguez Passage\nPort Jacobville, PR 3...  MediumAquaMarine   

   Avg. Session Length  Time on App  Time on Website  Length of Membership  \
0            34.497268    12.655651        39.577668              4.082621   
1            31.926272    11.109461        37.268959              2.664034   
2            33.000915    11.330278        37.110597              4.104543   
3            34.305557    13.717514        36.721283              3.120179   
4            33.330673    12.795189        37.536653              4.446308   

   Yearly Amount Spent  
0           587.951054  
1           392.204933  
2           487.547505  
3           581.852344  
4           599.406092

## 4) Helper Functions

Core functions that handle Safe Synthetics training and evaluation:

- **`run_safe_syn_training_with_builtin_holdout()`**: Creates and runs a Safe Synthetics job with automatic 5% holdout for evaluation
- **`get_quality_score_from_job()`**: Extracts the overall quality score from Safe Synthetics' built-in evaluation report  
- **`_extract_metric()`**: Utility function to safely extract nested metrics from evaluation reports


In [4]:
def run_safe_syn_training_with_builtin_holdout(params: Dict[str, Any], run_label: str) -> Any:
    """Create and run a Safe Synthetics job with the given parameters.
    
    Uses Safe Synthetics' built-in holdout (5%) and evaluation features.
    """
    # Create Safe Synthetics workflow with automatic holdout
    chain = (
        gretel.safe_synthetic_dataset
            .from_data_source(TRAINING_DATA_SOURCE, holdout=0.05)  # 5% automatic holdout
            .synthesize()  # Generate synthetic data
    )
    
    # Apply hyperparameters to the Safe Synthetics job
    try:
        chain = chain.with_parameters(params)
    except Exception:
        # Continue without parameters if not supported
        pass

    try:
        job = chain.create(run_name=run_label)
    except TypeError:
        job = chain.create()

    # Wait for job completion
    try:
        job.wait_until_done()
    except Exception:
        time.sleep(5)

    # Return the completed job (includes built-in evaluation)
    return job


def get_quality_score_from_job(job: Any) -> dict:
    """Extract quality and privacy scores from a completed Safe Synthetics job."""
    try:
        # For WorkflowRun objects, access the report directly
        if hasattr(job, 'report') and hasattr(job.report, 'dict'):
            report_dict = job.report.dict
            
            scores = {}
            if 'synthetic_quality_score' in report_dict:
                scores['quality_score'] = float(report_dict['synthetic_quality_score'])
            if 'data_privacy_score' in report_dict:
                scores['privacy_score'] = float(report_dict['data_privacy_score'])
                
            if scores:
                return scores
        
        raise RuntimeError("Could not extract scores from job report")
        
    except Exception as e:
        print(f"⚠️ Error extracting scores: {e}")
        raise

def evaluate_synthetic_vs_holdout(synthetic_file: Any, holdout_file: Any) -> Dict[str, Any]:
    wf = gretel.workflows.builder()
    wf.add_step(gretel.tasks.EvaluateSafeSyntheticsDataset(), [synthetic_file.id, holdout_file.id], step_name="evaluate")
    results = wf.run(wait_until_done=True)

    # Extract the evaluation report in a flexible way
    report = None
    # Newer SDKs: results.report.to_json()
    try:
        report = results.report.to_json()
    except Exception:
        pass
    # Named step output
    if report is None:
        try:
            report = results.outputs["evaluate"].report.to_json()
        except Exception:
            pass
    # Fallback to raw dict if available
    if report is None:
        report = getattr(results, "report", None)
    if report is None:
        raise RuntimeError("Could not retrieve evaluation report. Inspect `results`.")
    return report


def _extract_metric(report: Dict[str, Any], dotted_key: str) -> float:
    """Extract a nested metric value from an evaluation report using dot notation."""
    cur: Any = report
    for part in dotted_key.split("."):
        if not isinstance(cur, dict) or part not in cur:
            raise KeyError(f"Metric key '{dotted_key}' not found at '{part}'. Top-level keys: {list(cur.keys()) if isinstance(cur, dict) else cur}")
        cur = cur[part]
    if not isinstance(cur, (int, float)):
        raise TypeError(f"Metric '{dotted_key}' is not numeric: {cur}")
    return float(cur)


print("✅ Helper functions loaded:")
print("  - run_safe_syn_training_with_builtin_holdout: Creates Safe Synthetics jobs with automatic evaluation")
print("  - get_quality_score_from_job: Extracts quality scores from completed jobs") 
print("  - _extract_metric: Utility for parsing evaluation reports")
print("🚀 Ready for hyperparameter optimization!")


✅ Helper functions loaded:
  - run_safe_syn_training_with_builtin_holdout: Creates Safe Synthetics jobs with automatic evaluation
  - get_quality_score_from_job: Extracts quality scores from completed jobs
  - _extract_metric: Utility for parsing evaluation reports
🚀 Ready for hyperparameter optimization!


## 5) Hyperparameter Search Configuration

Define the parameter space for Bayesian optimization using Weights & Biases sweeps. This configuration specifies which Safe Synthetics parameters to optimize and their ranges.

**Optimization Strategy**: Bayesian optimization efficiently explores the parameter space to maximize synthetic data quality.


In [5]:
# W&B Sweep Configuration with Safe Synthetics + Tabular Fine-Tuning parameters
# Simplified flat structure for easier parameter passing
# Based on: https://docs.gretel.ai/create-synthetic-data/safe-synthetics/synthetics/gretel-tabular-fine-tuning
SWEEP_CONFIG = {
    "name": "safe-syn-tabular-ft-sweep",
    "method": "bayes",  # Bayesian optimization for efficient search
    "metric": {"name": "quality_score", "goal": "maximize"},
    "parameters": {
        # Safe Synthetics generation parameters
        "num_records": {
            "values": [500, 1000, 2000]  # Number of synthetic records to generate
        },
        
        # Core LoRA training parameters (flattened for easier passing)
        "learning_rate": {
            "min": 0.0001,
            "max": 0.001,
            "distribution": "log_uniform_values"
        },
        "batch_size": {
            "values": [1, 2, 4]  # Small batch sizes for tabular fine-tuning
        },
        "num_train_epochs": {
            "values": [3, 5, 8]  # Training epochs
        },
        "gradient_accumulation_steps": {
            "values": [4, 8, 16]
        },
        "weight_decay": {
            "min": 0.001,
            "max": 0.1,
            "distribution": "log_uniform_values"
        },
        "warmup_ratio": {
            "min": 0.01,
            "max": 0.1
        },
        
        # LoRA-specific parameters
        "lora_r": {
            "values": [16, 32, 64]  # LoRA rank - key parameter for adaptation
        },
        "lora_alpha": {
            "values": [16, 32, 64, 128]  # LoRA alpha parameter
        },
        "lora_dropout": {
            "min": 0.01,
            "max": 0.1
        },
        
        # Generation parameters
        "temperature": {
            "min": 0.7,
            "max": 1.0  # Controls randomness in generation
        },
        "top_p": {
            "min": 0.9,
            "max": 1.0  # Nucleus sampling parameter
        },
        "repetition_penalty": {
            "min": 1.0,
            "max": 1.2  # Prevents repetitive generation
        },
        
        # Data sampling
        "max_input_records": {
            "values": [5000, 10000, 25000]  # Input data sampling limit
        }
    },
    "early_terminate": {
        "type": "hyperband",
        "min_iter": 1
    }
}

print("🎯 W&B Sweep Configuration:")
print(json.dumps(SWEEP_CONFIG, indent=2))
print(f"\n✅ Sweep configured for {MAX_TRIALS} trials")
print(f"   - Method: {SWEEP_CONFIG['method']}")
print(f"   - Metric: {SWEEP_CONFIG['metric']['name']} ({SWEEP_CONFIG['metric']['goal']})")
print(f"   - Parameters: {len(SWEEP_CONFIG['parameters'])} hyperparameters")


🎯 W&B Sweep Configuration:
{
  "name": "safe-syn-tabular-ft-sweep",
  "method": "bayes",
  "metric": {
    "name": "quality_score",
    "goal": "maximize"
  },
  "parameters": {
    "num_records": {
      "values": [
        500,
        1000,
        2000
      ]
    },
    "learning_rate": {
      "min": 0.0001,
      "max": 0.001,
      "distribution": "log_uniform_values"
    },
    "batch_size": {
      "values": [
        1,
        2,
        4
      ]
    },
    "num_train_epochs": {
      "values": [
        3,
        5,
        8
      ]
    },
    "gradient_accumulation_steps": {
      "values": [
        4,
        8,
        16
      ]
    },
    "weight_decay": {
      "min": 0.001,
      "max": 0.1,
      "distribution": "log_uniform_values"
    },
    "warmup_ratio": {
      "min": 0.01,
      "max": 0.1
    },
    "lora_r": {
      "values": [
        16,
        32,
        64
      ]
    },
    "lora_alpha": {
      "values": [
        16,
        32,
        64,
  

## 6) Trial Execution Function

This function defines how each optimization trial runs. Each trial tests one unique set of parameters suggested by W&B's Bayesian optimization, allowing proper comparison between different parameter combinations.


In [6]:
def trial_agent():
    """Execute a single optimization trial with one set of parameters."""
    run = wandb.init(project=WANDB_PROJECT, entity=WANDB_ENTITY, name=f"{RUN_PREFIX}-{wandb.util.generate_id()}")
    params = dict(wandb.config)
    
    print(f"🚀 Starting trial: {run.name}")
    print(f"📊 Parameters: {params}")
    
    try:
        # Run a single Safe Synthetics job with this parameter set
        job = run_safe_syn_training_with_builtin_holdout(params=params, run_label=run.name)
        print(f"✅ Training complete!")
        
        # Extract quality score from built-in evaluation
        scores = get_quality_score_from_job(job)
        print(f"🎯 Quality score: {scores['quality_score']}")
        print(f"🔒 Privacy score: {scores['privacy_score']}")

        # Log results to Weights & Biases
        wandb.log({
            "quality_score": scores['quality_score'],
            "privacy_score": scores['privacy_score']
        })
        wandb.summary.update({
            "quality_score": scores['quality_score'],
            "privacy_score": scores['privacy_score']
        })
        
        print(f"✅ Trial complete → score={score}")
        
    except Exception as e:
        print(f"❌ Trial failed: {e}")
        wandb.log({"error": str(e)})
        raise
    finally:
        # Close the W&B run
        wandb.finish()


print("✅ Trial function ready:")
print(f"  - Each trial tests one unique parameter combination")
print(f"  - Uses automatic holdout and evaluation")  
print(f"  - Logs quality scores to Weights & Biases for comparison")
print("🚀 Ready to start hyperparameter optimization!")


✅ Trial function ready:
  - Each trial tests one unique parameter combination
  - Uses automatic holdout and evaluation
  - Logs quality scores to Weights & Biases for comparison
🚀 Ready to start hyperparameter optimization!


## 7) Configuration Summary

Review your current configuration settings before running the optimization.


In [7]:
# Display current configuration for review
print("📋 Current Configuration:")

print(f"📊 Dataset: {TRAINING_DATA_SOURCE}")
print(f"📈 Optimization trials: {MAX_TRIALS}")
print(f"🎯 Optimization method: {SWEEP_CONFIG['method']}")
print(f"📋 Parameters to optimize: {len(SWEEP_CONFIG['parameters'])}")

print(f"\n🔗 W&B Project: {WANDB_PROJECT}")
print(f"👤 W&B Entity: {WANDB_ENTITY}")

# Show key parameters being optimized
key_params = ['learning_rate', 'batch_size', 'temperature', 'lora_r', 'num_records']
print(f"\n🎛️ Key parameters being optimized:")
for param in key_params:
    if param in SWEEP_CONFIG['parameters']:
        config = SWEEP_CONFIG['parameters'][param]
        if 'values' in config:
            print(f"   - {param}: {config['values']}")
        elif 'min' in config and 'max' in config:
            print(f"   - {param}: {config['min']} to {config['max']}")

print(f"\n✅ Configuration ready for hyperparameter optimization!")


📋 Current Configuration:
📊 Dataset: https://gretel-datasets.s3.us-west-2.amazonaws.com/ecommerce_customers.csv
📈 Optimization trials: 2
🎯 Optimization method: bayes
📋 Parameters to optimize: 14

🔗 W&B Project: safe-syn-sweeps
👤 W&B Entity: yamini_gretel

🎛️ Key parameters being optimized:
   - learning_rate: 0.0001 to 0.001
   - batch_size: [1, 2, 4]
   - temperature: 0.7 to 1.0
   - lora_r: [16, 32, 64]
   - num_records: [500, 1000, 2000]

✅ Configuration ready for hyperparameter optimization!


## 8) Visualizing Results in W&B Dashboard

Tips for creating effective visualizations of your hyperparameter optimization results in the Weights & Biases dashboard.


In [ ]:
# W&B Dashboard Configuration Guide
print("📊 W&B Dashboard Configuration Tips")
print("=" * 50)

print("\n🎨 Creating Effective W&B Visualizations:")
print("1. Navigate to your W&B sweep dashboard")
print("2. Add recommended chart types for comprehensive analysis")
print("3. Use these panel configurations for best insights:")

print("\n📈 Recommended Dashboard Panels:")
print("┌─────────────────────────────────────────────────────────┐")
print("│ Panel Type          │ Metric Name          │ Description │")
print("├─────────────────────────────────────────────────────────┤")
print("│ Line Plot           │ quality_score        │ Main metric │")
print("│ Line Plot           │ privacy_score        │ Privacy metric │")
print("│ Scalar              │ final_quality_score  │ Final score │")
print("│ Bar Chart           │ trial_status         │ Run status  │")
print("│ Histogram           │ learning_rate        │ LR dist.    │")
print("│ Scatter Plot        │ temperature vs score │ Correlation │")
print("│ Table               │ All hyperparameters  │ Best runs   │")
print("│ Parallel Coordinates│ All params + score   │ Patterns    │")
print("└─────────────────────────────────────────────────────────┘")

print("\n🎯 Key Metrics to Track:")
metrics_info = {
    "quality_score": "Primary optimization metric (logged during run)",
    "privacy_score": "Privacy score (logged during run)",
    "final_quality_score": "Final score for each run (in summary)",
    "trial_status": "completed/failed status (string, not boolean)",
    "learning_rate": "Tabular FT learning rate",
    "batch_size": "Training batch size",
    "temperature": "Generation temperature",
    "lora_r": "LoRA rank parameter",
    "records_generated": "Number of synthetic records created",
    "error_message": "Error details for failed runs (string, not media)"
}

for metric, description in metrics_info.items():
    print(f"  • {metric:20} - {description}")

print("\n🚀 Pro Tips for W&B Visualization:")
print("  1. Use 'final_quality_score' for comparing final results")
print("  2. Use 'quality_score' for tracking optimization progress")
print("  3. Filter by 'trial_status' == 'completed' to exclude failed runs")
print("  4. Create scatter plots: 'learning_rate' vs 'final_quality_score'")
print("  5. Use parallel coordinates to find parameter patterns")

print("\n📋 Sample W&B Panel Configurations:")
print("```")
print("# Scatter Plot: Learning Rate vs Quality")
print("X-axis: learning_rate")
print("Y-axis: final_quality_score")
print("Color: batch_size")
print("Filter: trial_status == 'completed'")
print("")
print("# Parallel Coordinates: All Parameters")
print("Include: learning_rate, batch_size, temperature, lora_r, final_quality_score")
print("Color: final_quality_score")
print("```")

print(f"\n🔗 Access your sweep dashboard: https://wandb.ai/{WANDB_ENTITY or 'your-entity'}/{WANDB_PROJECT}")
print("✅ Use these visualizations to identify optimal parameter combinations!")


📊 W&B Dashboard Configuration Tips

🎨 Creating Effective W&B Visualizations:
1. Navigate to your W&B sweep dashboard
2. Add recommended chart types for comprehensive analysis
3. Use these panel configurations for best insights:

📈 Recommended Dashboard Panels:
┌─────────────────────────────────────────────────────────┐
│ Panel Type          │ Metric Name          │ Description │
├─────────────────────────────────────────────────────────┤
│ Line Plot           │ quality_score        │ Main metric │
│ Scalar              │ final_quality_score  │ Final score │
│ Bar Chart           │ trial_status         │ Run status  │
│ Histogram           │ learning_rate        │ LR dist.    │
│ Scatter Plot        │ temperature vs score │ Correlation │
│ Table               │ All hyperparameters  │ Best runs   │
│ Parallel Coordinates│ All params + score   │ Patterns    │
└─────────────────────────────────────────────────────────┘

🎯 Key Metrics to Track:
  • quality_score        - Primary optimizatio

## 9) Launch Hyperparameter Optimization

Start the Weights & Biases sweep to automatically optimize Safe Synthetics parameters. The sweep will run multiple trials, each testing different parameter combinations to find the best settings for your dataset.


In [10]:
# Launch the Weights & Biases sweep
print("🚀 Launching W&B Sweep...")
print(f"📋 Configuration: {MAX_TRIALS} trials using {SWEEP_CONFIG['method']} optimization")
print(f"🎯 Optimizing: {SWEEP_CONFIG['metric']['name']} ({SWEEP_CONFIG['metric']['goal']})")
print(f"📊 Dataset: {len(df)} rows, {len(df.columns)} columns")

try:
    # Create the sweep
    print("\n📝 Creating sweep...")
    sweep_id = wandb.sweep(SWEEP_CONFIG, project=WANDB_PROJECT, entity=WANDB_ENTITY)
    print(f"✅ Sweep created with ID: {sweep_id}")
    
    # Show sweep URL
    sweep_url = f"https://wandb.ai/{WANDB_ENTITY or 'your-entity'}/{WANDB_PROJECT}/sweeps/{sweep_id}"
    print(f"🔗 View sweep at: {sweep_url}")
    
    # Launch the agent
    print(f"\n🤖 Starting sweep agent (max {MAX_TRIALS} trials)...")
    print("=" * 80)
    
    start_time = time.time()
    wandb.agent(sweep_id, function=trial_agent, count=MAX_TRIALS)
    end_time = time.time()
    
    execution_time = end_time - start_time
    print("=" * 80)
    print("🏁 Sweep completed!")
    print(f"⏱️ Total execution time: {execution_time/60:.1f} minutes")
    print(f"📈 Average time per trial: {execution_time/MAX_TRIALS/60:.1f} minutes")
    print(f"🔗 Final results: {sweep_url}")
    
except Exception as e:
    print(f"❌ Sweep failed: {e}")
    print("Check the error details above and ensure all previous cells ran successfully.")
    raise

🚀 Launching W&B Sweep...
📋 Configuration: 2 trials using bayes optimization
🎯 Optimizing: quality_score (maximize)
📊 Dataset: 500 rows, 8 columns

📝 Creating sweep...
Create sweep with ID: e8o48dv0
Sweep URL: https://wandb.ai/yamini_gretel/safe-syn-sweeps/sweeps/e8o48dv0
✅ Sweep created with ID: e8o48dv0
🔗 View sweep at: https://wandb.ai/yamini_gretel/safe-syn-sweeps/sweeps/e8o48dv0

🤖 Starting sweep agent (max 2 trials)...


wandb: Agent Starting Run: dk0an880 with config:
wandb: 	batch_size: 2
wandb: 	gradient_accumulation_steps: 4
wandb: 	learning_rate: 0.0005028487963675808
wandb: 	lora_alpha: 16
wandb: 	lora_dropout: 0.07498826011840841
wandb: 	lora_r: 32
wandb: 	max_input_records: 5000
wandb: 	num_records: 1000
wandb: 	num_train_epochs: 3
wandb: 	repetition_penalty: 1.0997807762466294
wandb: 	temperature: 0.9576905174699012
wandb: 	top_p: 0.989535007770401
wandb: 	warmup_ratio: 0.06641367922936457
wandb: 	weight_decay: 0.0013366680486922313


🚀 Starting trial: safe-syn-lxmr1ys7
📊 Parameters: {'batch_size': 2, 'gradient_accumulation_steps': 4, 'learning_rate': 0.0005028487963675808, 'lora_alpha': 16, 'lora_dropout': 0.07498826011840841, 'lora_r': 32, 'max_input_records': 5000, 'num_records': 1000, 'num_train_epochs': 3, 'repetition_penalty': 1.0997807762466294, 'temperature': 0.9576905174699012, 'top_p': 0.989535007770401, 'warmup_ratio': 0.06641367922936457, 'weight_decay': 0.0013366680486922313}
Configuring generator for data source: https://gretel-datasets.s3.us-west-2.amazonaws.com/ecommerce_customers.csv
Configuring holdout: 0.05
Configuring synthetic data generation model: tabular_ft/default
▶️ Creating Workflow: w_31Fl4cur1ZouU3Yha3TgN4tKDj3
▶️ Created Workflow Run: wr_31Fl4deAXRL3OO8DIz7w82T2rXo
🔗 Workflow Run console link: https://console.gretel.ai/workflows/w_31Fl4cur1ZouU3Yha3TgN4tKDj3/runs/wr_31Fl4deAXRL3OO8DIz7w82T2rXo
Fetching task logs for workflow run wr_31Fl4deAXRL3OO8DIz7w82T2rXo
Workflow run is now in stat

Traceback (most recent call last):
  File "/Users/ykagal/.venvs/jupyter/lib/python3.13/site-packages/wandb/agents/pyagent.py", line 297, in _run_job
    self._function()
    ~~~~~~~~~~~~~~^^
  File "/var/folders/kx/_q607d_9603cg0389qczz_f00000gp/T/ipykernel_66388/2497270407.py", line 29, in trial_agent
    print(f"✅ Trial complete → score={score}")
                                       ^^^^^
NameError: name 'score' is not defined. Did you mean: 'scores'?

wandb: ERROR Run dk0an880 errored: name 'score' is not defined
wandb: Agent Starting Run: 9hww7mum with config:
wandb: 	batch_size: 2
wandb: 	gradient_accumulation_steps: 16
wandb: 	learning_rate: 0.00018847766722608427
wandb: 	lora_alpha: 64
wandb: 	lora_dropout: 0.08576453159743103
wandb: 	lora_r: 32
wandb: 	max_input_records: 5000
wandb: 	num_records: 2000
wandb: 	num_train_epochs: 5
wandb: 	repetition_penalty: 1.1397895049956188
wandb: 	temperature: 0.8948162775702677
wandb: 	top_p: 0.9971495213568616
wandb: 	warmup_ratio: 0.0590

🚀 Starting trial: safe-syn-pd0lrdry
📊 Parameters: {'batch_size': 2, 'gradient_accumulation_steps': 16, 'learning_rate': 0.00018847766722608427, 'lora_alpha': 64, 'lora_dropout': 0.08576453159743103, 'lora_r': 32, 'max_input_records': 5000, 'num_records': 2000, 'num_train_epochs': 5, 'repetition_penalty': 1.1397895049956188, 'temperature': 0.8948162775702677, 'top_p': 0.9971495213568616, 'warmup_ratio': 0.05901020017604965, 'weight_decay': 0.0018779079890300656}
Configuring generator for data source: https://gretel-datasets.s3.us-west-2.amazonaws.com/ecommerce_customers.csv
Configuring holdout: 0.05
Configuring synthetic data generation model: tabular_ft/default
▶️ Using Workflow: w_31Fl4cur1ZouU3Yha3TgN4tKDj3
▶️ Created Workflow Run: wr_31FoaHOmzhLPJ1bS3slOOUGpwlA
🔗 Workflow Run console link: https://console.gretel.ai/workflows/w_31Fl4cur1ZouU3Yha3TgN4tKDj3/runs/wr_31FoaHOmzhLPJ1bS3slOOUGpwlA
Fetching task logs for workflow run wr_31FoaHOmzhLPJ1bS3slOOUGpwlA
Workflow run is now in stat

Traceback (most recent call last):
  File "/Users/ykagal/.venvs/jupyter/lib/python3.13/site-packages/wandb/agents/pyagent.py", line 297, in _run_job
    self._function()
    ~~~~~~~~~~~~~~^^
  File "/var/folders/kx/_q607d_9603cg0389qczz_f00000gp/T/ipykernel_66388/2497270407.py", line 29, in trial_agent
    print(f"✅ Trial complete → score={score}")
                                       ^^^^^
NameError: name 'score' is not defined. Did you mean: 'scores'?

wandb: ERROR Run 9hww7mum errored: name 'score' is not defined


🏁 Sweep completed!
⏱️ Total execution time: 52.0 minutes
📈 Average time per trial: 26.0 minutes
🔗 Final results: https://wandb.ai/yamini_gretel/safe-syn-sweeps/sweeps/e8o48dv0


## Tests for Debugging

In [ ]:
# Check what variables are in memory from the recent trial runs
print("🔍 Checking available variables...")

# List all variables in the global namespace
variables = [var for var in globals().keys() if not var.startswith('_')]
print(f"📋 Available variables: {variables}")

# Look for any job-related variables
job_vars = [var for var in variables if 'job' in var.lower()]
print(f"🎯 Job-related variables: {job_vars}")

# Check if there are any gretel-related objects
gretel_vars = [var for var in variables if any(keyword in str(type(globals()[var])).lower() 
                                              for keyword in ['gretel', 'synthetic', 'workflow'])]
print(f"🔧 Gretel-related variables: {gretel_vars}")

# If you see any promising variables, inspect them:
for var in gretel_vars[:3]:  # Check first 3
    try:
        obj = globals()[var]
        print(f"\n📊 {var}: {type(obj)}")
        if hasattr(obj, 'report'):
            print(f"   ✅ Has report attribute")
        if hasattr(obj, 'id'):
            print(f"   🆔 ID: {obj.id}")
    except:
        pass

In [ ]:
# Test to extract quality and privacy scores
print(f"🔍 Testing score extraction for: {job_id}")

try:
    workflow_run = gretel.workflows.get_workflow_run(job_id)
    report_dict = workflow_run.report.dict
    
    # Extract quality score
    quality_score = report_dict['synthetic_quality_score']
    print(f"🎯 Quality Score: {quality_score}")
    
    # Extract privacy score  
    privacy_score = report_dict['data_privacy_score']
    print(f"🔒 Privacy Score: {privacy_score}")
    
    # Show other available scores for reference
    print(f"\n📊 Other available scores:")
    score_keys = [k for k in report_dict.keys() if 'score' in k.lower()]
    for key in score_keys:
        print(f"   - {key}: {report_dict[key]}")
    
    print(f"\n✅ SUCCESS! Both scores extracted successfully.")
    print(f"   Quality: {quality_score}, Privacy: {privacy_score}")
    
except Exception as e:
    print(f"❌ Error: {e}")

## 10) Results Summary


In [ ]:
# Optional: Analyze sweep results programmatically
print("📊 Analyzing sweep results...")

try:
    # Get sweep results from W&B API
    sweep = api.sweep(f"{WANDB_ENTITY}/{WANDB_PROJECT}/{sweep_id}")
    runs = list(sweep.runs)
    
    print(f"\n✅ Sweep completed with {len(runs)} runs")
    
    # Find best run
    completed_runs = [run for run in runs if run.state == "finished"]
    
    if completed_runs:
        best_run = max(completed_runs, key=lambda r: r.summary.get("quality_score", 0))
        
        print(f"\n🏆 Best run: {best_run.name}")
        print(f"   - Quality Score: {best_run.summary.get('quality_score', 'N/A')}")
        print(f"   - Learning Rate: {best_run.config.get('learning_rate', 'N/A')}")
        print(f"   - Batch Size: {best_run.config.get('batch_size', 'N/A')}")
        print(f"   - Temperature: {best_run.config.get('temperature', 'N/A')}")
        print(f"   - LoRA R: {best_run.config.get('lora_r', 'N/A')}")
        print(f"   - Worker ID: {best_run.summary.get('worker_id', 'N/A')}")
        print(f"   - Run URL: {best_run.url}")
        
        # Summary statistics
        quality_scores = [run.summary.get("quality_score", 0) for run in completed_runs]
        worker_ids = [run.summary.get("worker_id", 0) for run in completed_runs]
        
        print(f"\n📈 Quality Score Statistics:")
        print(f"   - Best: {max(quality_scores):.4f}")
        print(f"   - Worst: {min(quality_scores):.4f}")
        print(f"   - Average: {sum(quality_scores)/len(quality_scores):.4f}")
        print(f"   - Standard Deviation: {(sum((x - sum(quality_scores)/len(quality_scores))**2 for x in quality_scores) / len(quality_scores))**0.5:.4f}")
        
    failed_runs = [run for run in runs if run.state == "failed"]
    if failed_runs:
        print(f"\n⚠️ {len(failed_runs)} run(s) failed")
        for run in failed_runs:
            print(f"   - {run.name}: {run.summary.get('error_message', 'Unknown error')}")

except Exception as e:
    print(f"⚠️ Could not analyze results: {e}")
    print(f"You can view results manually at: https://wandb.ai/{WANDB_ENTITY}/{WANDB_PROJECT}")

print("\n🎉 Safe Synthetics sweep completed!")
print("\nKey improvements in this version:")
print("✅ Removed slow holdout/transform steps")
print("✅ Direct Safe Synthetics workflow")
print("✅ Tabular Fine-Tuning parameter optimization")
print("✅ Enhanced W&B logging and error handling")
print("✅ Comprehensive quality score extraction")
print("\n📝 Configuration options:")
print("  - Set MAX_TRIALS=N to change number of trials")
